#Predicting sentiment from product reviews

#Fire up GraphLab Create

In [1]:
import graphlab

#Read some product review data

Loading reviews for a set of baby products. 

In [78]:
products = graphlab.SFrame('amazon_baby.gl/')

#Let's explore this data together

Data includes the product name, the review text and the rating of the review. 

In [79]:
products.head()

Columns:
	name	str
	review	str
	rating	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|    Planetwise Flannel Wipes   | These flannel wipes are OK... |  3.0   |
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
+-------------------------------+-------------------------------+--------+
[10 rows x 3 columns]

#Build the word count vector for each review

In [80]:
products['word_count'] = graphlab.text_analytics.count_words(products['review'])

In [81]:
products.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|    Planetwise Flannel Wipes   | These flannel wipes are OK... |  3.0   |
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+
|           word_count          |
+-------------------------------+
| {'and': 5, 'stink': 1, 'be... |
| {'and': 3, 'love': 1, 'it'... |
| {'and': 2, 'quilt': 1, 'it... |
| {'ingenious': 1, 'and': 3,... |
| {'and': 2, 'parents!!': 1,... |
| {'and': 2, 'cute': 1, 'hel... |
| {'shop': 1, 'be': 1, 'is':... |
| {'feeding,': 1, 'and': 2, ... |
| {'and': 1, 'help': 1, 'giv... |
| {'journal.': 1, 'all': 1, ... |
+-------------------------------+
[10 rows x 4 columns]

In [6]:
graphlab.canvas.set_target('ipynb')

In [7]:
products['name'].show()

#Examining the reviews for most-sold product:  'Vulli Sophie the Giraffe Teether'

In [8]:
giraffe_reviews = products[products['name'] == 'Vulli Sophie the Giraffe Teether']

In [9]:
len(giraffe_reviews)

785

In [10]:
giraffe_reviews['rating'].show(view='Categorical')

#Build a sentiment classifier

In [11]:
products['rating'].show(view='Categorical')

##Define what's a positive and a negative sentiment

We will ignore all reviews with rating = 3, since they tend to have a neutral sentiment.  Reviews with a rating of 4 or higher will be considered positive, while the ones with rating of 2 or lower will have a negative sentiment.   

In [12]:
#ignore all 3* reviews
products = products[products['rating'] != 3]

In [13]:
#positive sentiment = 4* or 5* reviews
products['sentiment'] = products['rating'] >=4

In [14]:
products.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	sentiment	int

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
|     Planetwise Wipe Pouch     | it came early and was not ... |  5.0   |
| Annas Dream Full Quilt wit... | Very soft and comfortable ... |  5.0   |
| Stop Pacifier Sucking with... | This is a product well wor... |  5.0   |
| Stop Pacifier Sucking with... | All of my kids have cried ... |  5.0   |
| Stop Pacifier Sucking with... | When the Binky Fairy came ... |  5.0   |
| A Tale of Baby's Days with... | Lovely book, it's bound ti... |  4.0   |
| Baby Tracker&reg; - Daily ... | Perfect for new parents. W... |  5.0   |
| Baby Tracker&reg; - Daily ... | A friend of mine pinned th... |  5.0   |
| Baby Tracker&reg; - Daily ... | This has been an easy way ... |  4.0   |
| Baby Tracker&reg; - Daily ... | I love this journal and ou... |  4.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+-----------+
|           word_count          | sentiment |
+-------------------------------+-----------+
| {'and': 3, 'love': 1, 'it'... |     1     |
| {'and': 2, 'quilt': 1, 'it... |     1     |
| {'ingenious': 1, 'and': 3,... |     1     |
| {'and': 2, 'parents!!': 1,... |     1     |
| {'and': 2, 'cute': 1, 'hel... |     1     |
| {'shop': 1, 'be': 1, 'is':... |     1     |
| {'feeding,': 1, 'and': 2, ... |     1     |
| {'and': 1, 'help': 1, 'giv... |     1     |
| {'journal.': 1, 'all': 1, ... |     1     |
| {'all': 1, 'forget': 1, 'j... |     1     |
+-------------------------------+-----------+
[10 rows x 5 columns]

##Let's train the sentiment classifier

In [15]:
train_data,test_data = products.random_split(.8, seed=0)

In [16]:
sentiment_model = graphlab.logistic_classifier.create(train_data,
                                                     target='sentiment',
                                                     features=['word_count'],
                                                     validation_set=test_data)

PROGRESS: Logistic regression:
PROGRESS: --------------------------------------------------------
PROGRESS: Number of examples          : 133448
PROGRESS: Number of classes           : 2
PROGRESS: Number of feature columns   : 1
PROGRESS: Number of unpacked features : 219217
PROGRESS: Number of coefficients    : 219218
PROGRESS: Starting L-BFGS
PROGRESS: --------------------------------------------------------
PROGRESS: +-----------+----------+-----------+--------------+-------------------+---------------------+
PROGRESS: | Iteration | Passes   | Step size | Elapsed Time | Training-accuracy | Validation-accuracy |
PROGRESS: +-----------+----------+-----------+--------------+-------------------+---------------------+
PROGRESS: | 1         | 5        | 0.000002  | 4.460335     | 0.841481          | 0.839989            |
PROGRESS: | 2         | 9        | 3.000000  | 7.859937     | 0.947425          | 0.894877            |
PROGRESS: | 3         | 10       | 3.000000  | 9.220890     | 0.92

#Evaluate the sentiment model

In [17]:
sentiment_model.evaluate(test_data, metric='roc_curve')

{'roc_curve': Columns:
 	threshold	float
 	fpr	float
 	tpr	float
 	p	int
 	n	int
 
 Rows: 1001
 
 Data:
 +------------------+----------------+------------------+-------+------+
 |    threshold     |      fpr       |       tpr        |   p   |  n   |
 +------------------+----------------+------------------+-------+------+
 |       0.0        | 0.224558768306 | 0.00364441903673 | 27988 | 5326 |
 | 0.0010000000475  | 0.775441231694 |  0.996355580963  | 27988 | 5326 |
 | 0.00200000009499 | 0.73544874202  |  0.99531942261   | 27988 | 5326 |
 | 0.00300000002608 | 0.712730003755 |  0.994712019437  | 27988 | 5326 |
 | 0.00400000018999 | 0.697146075854 |  0.994247534658  | 27988 | 5326 |
 | 0.00499999988824 | 0.685880585805 |  0.993890238674  | 27988 | 5326 |
 | 0.00600000005215 | 0.676117161097 |  0.993390024296  | 27988 | 5326 |
 | 0.00700000021607 | 0.665602703718 |  0.993032728312  | 27988 | 5326 |
 | 0.00800000037998 | 0.655276004506 |  0.992782621123  | 27988 | 5326 |
 | 0.00899999961257 

In [18]:
sentiment_model.show(view='Evaluation')

#Applying the learned model to understand sentiment for Giraffe

In [19]:
giraffe_reviews['predicted_sentiment'] = sentiment_model.predict(giraffe_reviews, output_type='probability')

In [20]:
giraffe_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
| Vulli Sophie the Giraffe T... | He likes chewing on all th... |  5.0   |
| Vulli Sophie the Giraffe T... | My son loves this toy and ... |  5.0   |
| Vulli Sophie the Giraffe T... | There really should be a l... |  1.0   |
| Vulli Sophie the Giraffe T... | All the moms in my moms' g... |  5.0   |
| Vulli Sophie the Giraffe T... | I was a little skeptical o... |  5.0   |
| Vulli Sophie the Giraffe T... | I have been reading about ... |  5.0   |
| Vulli Sophie the Giraffe T... | My neice loves her sophie ... |  5.0   |
| Vulli Sophie the Giraffe T... | What a friendly face!  And... |  5.0   |
| Vulli Sophie the Giraffe T... | We got this just for my so... |  5.0   |
| Vulli Sophie the Giraffe T... | My baby seems to like this... |  3.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+---------------------+
|           word_count          | predicted_sentiment |
+-------------------------------+---------------------+
| {'and': 1, 'all': 1, 'beca... |    0.999513023521   |
| {'and': 1, 'right': 1, 'he... |    0.999320678306   |
| {'and': 2, 'all': 1, 'late... |    0.013558811687   |
| {'and': 2, 'one!': 1, 'all... |    0.995769474148   |
| {'and': 3, 'all': 1, 'old'... |    0.662374415673   |
| {'and': 6, 'seven': 1, 'al... |    0.999997148186   |
| {'and': 4, 'drooling,': 1,... |    0.989190989536   |
| {'and': 3, 'chew': 1, "don... |    0.999563518413   |
| {'chew': 2, 'because': 1, ... |    0.970160542725   |
| {'and': 2, 'already': 1, '... |    0.195367644588   |
+-------------------------------+---------------------+
[10 rows x 5 columns]

##Sort the reviews based on the predicted sentiment and explore

In [21]:
giraffe_reviews = giraffe_reviews.sort('predicted_sentiment', ascending=False)

In [22]:
giraffe_reviews.head()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	predicted_sentiment	float

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
| Vulli Sophie the Giraffe T... | Sophie, oh Sophie, your ti... |  5.0   |
| Vulli Sophie the Giraffe T... | I'm not sure why Sophie is... |  4.0   |
| Vulli Sophie the Giraffe T... | I'll be honest...I bought ... |  4.0   |
| Vulli Sophie the Giraffe T... | We got this little giraffe... |  5.0   |
| Vulli Sophie the Giraffe T... | As a mother of 16month old... |  5.0   |
| Vulli Sophie the Giraffe T... | Sophie the Giraffe is the ... |  5.0   |
| Vulli Sophie the Giraffe T... | Sophie la giraffe is absol... |  5.0   |
| Vulli Sophie the Giraffe T... | My 5-mos old son took to t... |  5.0   |
| Vulli Sophie the Giraffe T... | My nephews and my four kid... |  5.0   |
| Vulli Sophie the Giraffe T... | Never thought I'd see my s... |  5.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+---------------------+
|           word_count          | predicted_sentiment |
+-------------------------------+---------------------+
| {'giggles': 1, 'all': 1, "... |         1.0         |
| {'peace': 1, 'month': 1, '... |    0.999999999703   |
| {'all': 2, 'pops': 1, 'exi... |    0.999999999392   |
| {'all': 2, "don't": 1, '(l... |    0.99999999919    |
| {'cute': 1, 'all': 1, 'rev... |    0.999999998657   |
| {'just': 2, 'both': 1, 'mo... |    0.999999997108   |
| {'and': 5, 'the': 1, 'all'... |    0.999999995589   |
| {'just': 1, 'shape': 2, 'm... |    0.999999995573   |
| {'and': 4, 'chew': 1, 'all... |    0.999999989527   |
| {'giggles': 1, 'all': 1, '... |    0.999999985069   |
+-------------------------------+---------------------+
[10 rows x 5 columns]

##Most positive reviews for the giraffe

In [23]:
giraffe_reviews[0]['review']

"Sophie, oh Sophie, your time has come. My granddaughter, Violet is 5 months old and starting to teeth. What joy little Sophie brings to Violet. Sophie is made of a very pliable rubber that is sturdy but not tough. It is quite easy for Violet to twist Sophie into unheard of positions to get Sophie into her mouth. The little nose and hooves fit perfectly into small mouths, and the drooling has purpose. The paint on Sophie is food quality.Sophie was born in 1961 in France. The maker had wondered why there was nothing available for babies and made Sophie from the finest rubber, phthalate-free on St Sophie's Day, thus the name was born. Since that time millions of Sophie's populate the world. She is soft and for babies little hands easy to grasp. Violet especially loves the bumpy head and horns of Sophie. Sophie has a long neck that easy to grasp and twist. She has lovely, sizable spots that attract Violet's attention. Sophie has happy little squeaks that bring squeals of delight from Viol

In [24]:
giraffe_reviews[1]['review']

"I'm not sure why Sophie is such a hit with the little ones, but my 7 month old baby girl is one of her adoring fans.  The rubber is softer and more pleasant to handle, and my daughter has enjoyed chewing on her legs and the nubs on her head even before she started teething.  She also loves the squeak that Sophie makes when you squeeze her.  Not sure what it is but if Sophie is amongst a pile of her other toys, my daughter will more often than not reach for Sophie.  And I have the peace of mind of knowing that only edible and safe paints and materials have been used to make Sophie, as opposed to Bright Starts and other baby toys made in China.  Now that the research is out on phthalates and other toxic substances in baby toys, I think it's more important than ever to find good quality toys that are also safe for our babies to handle and put in their mouths.  Sophie is a must-have for every new mom in my opinion.  Even if your kid is one of the few that can take or leave her, it's worth

##Show most negative reviews for giraffe

In [25]:
giraffe_reviews[-1]['review']

"My son (now 2.5) LOVED his Sophie, and I bought one for every baby shower I've gone to. Now, my daughter (6 months) just today nearly choked on it and I will never give it to her again. Had I not been within hearing range it could have been fatal. The strange sound she was making caught my attention and when I went to her and found the front curved leg shoved well down her throat and her face a purply/blue I panicked. I pulled it out and she vomited all over the carpet before screaming her head off. I can't believe how my opinion of this toy has changed from a must-have to a must-not-use. Please don't disregard any of the choking hazard comments, they are not over exaggerated!"

In [26]:
giraffe_reviews[-2]['review']

"This children's toy is nostalgic and very cute. However, there is a distinct rubber smell and a very odd taste, yes I tried it, that my baby did not enjoy. Also, if it is soiled it is extremely difficult to clean as the rubber is a kind of porus material and does not clean well. The final thing is the squeaking device inside which stopped working after the first couple of days. I returned this item feeling I had overpaid for a toy that was defective and did not meet my expectations. Please do not be swayed by the cute packaging and hype surounding it as I was. One more thing, I was given a full refund from Amazon without any problem."

In [27]:
test_string = 'last'

In [30]:
test_string

'first'

In [82]:
selected_words = ['awesome', 'great', 'fantastic', 'amazing', 'love', 'horrible', 'bad', 'terrible', 'awful', 'wow', 'hate']

def current_selected_word_count(word_count):
    if current_selected_word in word_count:
        return word_count[current_selected_word]
    return 0

current_selected_word = ''
for current_selected_word in selected_words:
    products[current_selected_word] = products['word_count'].apply(current_selected_word_count)

In [84]:
products.tail()

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	awesome	int
	great	int
	fantastic	int
	amazing	int
	love	int
	horrible	int
	bad	int
	terrible	int
	awful	int
	wow	int
	hate	int

Rows: 10

Data:
+-------------------------------+-------------------------------+--------+
|              name             |             review            | rating |
+-------------------------------+-------------------------------+--------+
| Airline Seat Belt Extender... | Up until recently I have h... |  5.0   |
| Airline Seat Belt Extender... | I bought this as a father'... |  5.0   |
| Squeasy Snacker 6oz Silico... | I love that these can hold... |  5.0   |
| Squeasy Snacker 6oz Silico... | I love this product, it ma... |  5.0   |
| Squeasy Snacker 6oz Silico... | This reusable squeeze bott... |  5.0   |
| Baby Teething Necklace for... | Such a great idea! very ha... |  5.0   |
| Baby Teething Necklace for... | This product rocks!  It is... |  5.0   |
| Abstract 2 PK Baby / Toddl... | This item looks great and ... |  5.0   |
| Baby Food Freezer Tray - B... | I am extremely happy with ... |  5.0   |
| Best 2 Pack Baby Car Shade... | I love this product very m... |  5.0   |
+-------------------------------+-------------------------------+--------+
+-------------------------------+---------+-------+-----------+---------+------+
|           word_count          | awesome | great | fantastic | amazing | love |
+-------------------------------+---------+-------+-----------+---------+------+
| {'and': 1, 'uncomfortable'... |    0    |   0   |     0     |    0    |  0   |
| {'and': 4, 'it.': 1, 'beca... |    0    |   0   |     0     |    0    |  0   |
| {'and': 5, 'right': 1, 'lo... |    0    |   1   |     0     |    0    |  2   |
| {'and': 6, 'love': 1, 'fam... |    0    |   1   |     0     |    0    |  1   |
| {'when': 2, 'through': 1, ... |    1    |   0   |     0     |    0    |  1   |
| {'and': 1, 'help': 1, 'too... |    0    |   2   |     0     |    0    |  0   |
| {'accessible': 1, 'and': 5... |    0    |   1   |     0     |    0    |  0   |
| {'and': 2, 'great': 2, 'ki... |    0    |   2   |     0     |    0    |  0   |
| {'just': 1, 'bimbi': 2, 'o... |    0    |   0   |     0     |    0    |  0   |
| {'and': 1, 'love': 1, 'sha... |    0    |   0   |     0     |    0    |  1   |
+-------------------------------+---------+-------+-----------+---------+------+
+----------+-----+----------+-------+-----+------+
| horrible | bad | terrible | awful | wow | hate |
+----------+-----+----------+-------+-----+------+
|    0     |  0  |    0     |   0   |  0  |  0   |
|    0     |  0  |    0     |   0   |  0  |  0   |
|    0     |  0  |    0     |   0   |  0  |  0   |
|    0     |  0  |    0     |   0   |  0  |  0   |
|    0     |  0  |    0     |   0   |  0  |  0   |
|    0     |  0  |    0     |   0   |  0  |  0   |
|    0     |  0  |    0     |   0   |  0  |  0   |
|    0     |  0  |    0     |   0   |  0  |  0   |
|    0     |  0  |    0     |   0   |  0  |  0   |
|    0     |  0  |    0     |   0   |  0  |  0   |
+----------+-----+----------+-------+-----+------+
[10 rows x 15 columns]

In [85]:
selected_words_sums = {}
for selected_word in selected_words:
    selected_words_sums[selected_word] = products[selected_word].sum()

In [86]:
selected_words_sums

{'amazing': 1363,
 'awesome': 2090,
 'awful': 383,
 'bad': 3724,
 'fantastic': 932,
 'great': 45206,
 'hate': 1220,
 'horrible': 734,
 'love': 42065,
 'terrible': 748,
 'wow': 144}

In [88]:
#ignore all 3* reviews
products = products[products['rating'] != 3]
#positive sentiment = 4* or 5* reviews
products['sentiment'] = products['rating'] >=4

train_data,test_data = products.random_split(.8, seed=0)
selected_words_model = graphlab.logistic_classifier.create(train_data,
                                                     target='sentiment',
                                                     features=selected_words,
                                                     validation_set=test_data)

PROGRESS: Logistic regression:
PROGRESS: --------------------------------------------------------
PROGRESS: Number of examples          : 133448
PROGRESS: Number of classes           : 2
PROGRESS: Number of feature columns   : 11
PROGRESS: Number of unpacked features : 11
PROGRESS: Number of coefficients    : 12
PROGRESS: Starting Newton Method
PROGRESS: --------------------------------------------------------
PROGRESS: +-----------+----------+--------------+-------------------+---------------------+
PROGRESS: | Iteration | Passes   | Elapsed Time | Training-accuracy | Validation-accuracy |
PROGRESS: +-----------+----------+--------------+-------------------+---------------------+
PROGRESS: | 1         | 2        | 0.652783     | 0.844299          | 0.842842            |
PROGRESS: | 2         | 3        | 1.143585     | 0.844186          | 0.842842            |
PROGRESS: | 3         | 4        | 1.664534     | 0.844276          | 0.843142            |
PROGRESS: | 4         | 5        |

In [89]:
selected_words_model['coefficients']

Columns:
	name	str
	index	str
	class	int
	value	float

Rows: 12

Data:
+-------------+-------+-------+-----------------+
|     name    | index | class |      value      |
+-------------+-------+-------+-----------------+
| (intercept) |  None |   1   |  1.36728315229  |
|   awesome   |  None |   1   |  1.05800888878  |
|    great    |  None |   1   |  0.883937894898 |
|  fantastic  |  None |   1   |  0.891303090304 |
|   amazing   |  None |   1   |  0.892802422509 |
|     love    |  None |   1   |  1.39989834302  |
|   horrible  |  None |   1   |  -1.99651800559 |
|     bad     |  None |   1   | -0.985827369929 |
|   terrible  |  None |   1   |  -2.09049998487 |
|    awful    |  None |   1   |  -1.76469955631 |
+-------------+-------+-------+-----------------+
[12 rows x 4 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [90]:
selected_words_model['coefficients'].sort('value')

Columns:
	name	str
	index	str
	class	int
	value	float

Rows: 12

Data:
+-----------+-------+-------+------------------+
|    name   | index | class |      value       |
+-----------+-------+-------+------------------+
|  terrible |  None |   1   |  -2.09049998487  |
|  horrible |  None |   1   |  -1.99651800559  |
|   awful   |  None |   1   |  -1.76469955631  |
|    hate   |  None |   1   |  -1.40916406276  |
|    bad    |  None |   1   | -0.985827369929  |
|    wow    |  None |   1   | -0.0541450123332 |
|   great   |  None |   1   |  0.883937894898  |
| fantastic |  None |   1   |  0.891303090304  |
|  amazing  |  None |   1   |  0.892802422509  |
|  awesome  |  None |   1   |  1.05800888878   |
+-----------+-------+-------+------------------+
[12 rows x 4 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [91]:
selected_words_model['coefficients'].sort('value', ascending=False)

Columns:
	name	str
	index	str
	class	int
	value	float

Rows: 12

Data:
+-------------+-------+-------+------------------+
|     name    | index | class |      value       |
+-------------+-------+-------+------------------+
|     love    |  None |   1   |  1.39989834302   |
| (intercept) |  None |   1   |  1.36728315229   |
|   awesome   |  None |   1   |  1.05800888878   |
|   amazing   |  None |   1   |  0.892802422509  |
|  fantastic  |  None |   1   |  0.891303090304  |
|    great    |  None |   1   |  0.883937894898  |
|     wow     |  None |   1   | -0.0541450123332 |
|     bad     |  None |   1   | -0.985827369929  |
|     hate    |  None |   1   |  -1.40916406276  |
|    awful    |  None |   1   |  -1.76469955631  |
+-------------+-------+-------+------------------+
[12 rows x 4 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [92]:
selected_words_model.evaluate(test_data, metric='roc_curve')

{'roc_curve': Columns:
 	threshold	float
 	fpr	float
 	tpr	float
 	p	int
 	n	int
 
 Rows: 1001
 
 Data:
 +------------------+------------------+-----+-------+------+
 |    threshold     |       fpr        | tpr |   p   |  n   |
 +------------------+------------------+-----+-------+------+
 |       0.0        | 0.00018765246763 | 0.0 | 27976 | 5329 |
 | 0.0010000000475  |  0.999812347532  | 1.0 | 27976 | 5329 |
 | 0.00200000009499 |  0.999624695065  | 1.0 | 27976 | 5329 |
 | 0.00300000002608 |  0.999624695065  | 1.0 | 27976 | 5329 |
 | 0.00400000018999 |  0.999437042597  | 1.0 | 27976 | 5329 |
 | 0.00499999988824 |  0.999437042597  | 1.0 | 27976 | 5329 |
 | 0.00600000005215 |  0.999249390129  | 1.0 | 27976 | 5329 |
 | 0.00700000021607 |  0.999249390129  | 1.0 | 27976 | 5329 |
 | 0.00800000037998 |  0.999249390129  | 1.0 | 27976 | 5329 |
 | 0.00899999961257 |  0.999249390129  | 1.0 | 27976 | 5329 |
 +------------------+------------------+-----+-------+------+
 [1001 rows x 5 columns]
 No

In [93]:
selected_words_model.show(view='Evaluation')

In [94]:
diaper_champ_reviews = products[products['name'] == 'Baby Trend Diaper Champ']
len(diaper_champ_reviews)

298

In [99]:
diaper_champ_reviews['predicted_sentiment'] = sentiment_model.predict(diaper_champ_reviews, output_type='probability')
diaper_champ_reviews.sort('predicted_sentiment', ascending=False)[0]['review']

'Baby Luke can turn a clean diaper to a dirty diaper in 3 seconds flat. The diaper champ turns the smelly diaper into "what diaper smell" in less time than that. I hesitated and wondered what I REALLY needed for the nursery. This is one of the best purchases we made. The champ, the baby bjorn, fluerville diaper bag, and graco pack and play bassinet all vie for the best baby purchase.Great product, easy to use, economical, effective, absolutly fabulous.UpdateI knew that I loved the champ, and useing the diaper genie at a friend\'s house REALLY reinforced that!! There is no comparison, the chanp is easy and smell free, the genie was difficult to use one handed (which is absolutly vital if you have a little one on a changing pad) and there was a deffinite odor eminating from the genieplus we found that the quick tie garbage bags where the ties are integrated into the bag work really well because there isn\'t any added bulk around the sealing edge of the champ.'

In [96]:
diaper_champ_reviews['predicted_sentiment'] = selected_words_model.predict(diaper_champ_reviews, output_type='probability')
diaper_champ_reviews.sort('predicted_sentiment', ascending=False)

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	awesome	int
	great	int
	fantastic	int
	amazing	int
	love	int
	horrible	int
	bad	int
	terrible	int
	awful	int
	wow	int
	hate	int
	sentiment	int
	predicted_sentiment	float

Rows: 298

Data:
+-------------------------+-------------------------------+--------+
|           name          |             review            | rating |
+-------------------------+-------------------------------+--------+
| Baby Trend Diaper Champ | I LOVE LOVE LOVE this prod... |  4.0   |
| Baby Trend Diaper Champ | I received my Diaper Champ... |  5.0   |
| Baby Trend Diaper Champ | Love it, love it, love it!... |  5.0   |
| Baby Trend Diaper Champ | Works great - no smells.  ... |  5.0   |
| Baby Trend Diaper Champ | I love this diaper pale an... |  5.0   |
| Baby Trend Diaper Champ | We had 2 diaper Genie's bo... |  4.0   |
| Baby Trend Diaper Champ | I've worked with kids more... |  5.0   |
| Baby Trend Diaper Champ | This is absolutely, by far... |  5.0   |
| Baby Trend Diaper Champ | I have a two-year-old son ... |  5.0   |
| Baby Trend Diaper Champ | I love this diaper pail!  ... |  5.0   |
+-------------------------+-------------------------------+--------+
+-------------------------------+---------+-------+-----------+---------+------+
|           word_count          | awesome | great | fantastic | amazing | love |
+-------------------------------+---------+-------+-----------+---------+------+
| {'rating': 1, 'contacted':... |    0    |   1   |     0     |    0    |  3   |
| {'bags.': 1, "don't": 1, '... |    0    |   0   |     0     |    0    |  3   |
| {'all': 1, 'already': 1, '... |    0    |   0   |     0     |    0    |  3   |
| {'and': 2, 'love': 1, 'gar... |    0    |   2   |     0     |    0    |  1   |
| {'and': 3, 'love': 1, 'use... |    0    |   2   |     0     |    0    |  1   |
| {'hand.': 1, '(required': ... |    0    |   0   |     0     |    0    |  2   |
| {'and': 4, 'genies': 1, 'n... |    0    |   0   |     0     |    0    |  2   |
| {'just': 3, 'money': 1, 'n... |    0    |   0   |     0     |    0    |  2   |
| {'and': 6, 'two-year-old':... |    0    |   0   |     0     |    0    |  2   |
| {'and': 3, 'this': 1, 'lov... |    0    |   0   |     0     |    0    |  2   |
+-------------------------------+---------+-------+-----------+---------+------+
+----------+-----+----------+-------+-----+------+-----------+---------------------+
| horrible | bad | terrible | awful | wow | hate | sentiment | predicted_sentiment |
+----------+-----+----------+-------+-----+------+-----------+---------------------+
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.998423414594   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.996192539732   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.996192539732   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.989387539605   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.989387539605   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.984739056527   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.984739056527   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.984739056527   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.984739056527   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.984739056527   |
+----------+-----+----------+-------+-----+------+-----------+---------------------+
[298 rows x 17 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [97]:
diaper_champ_reviews.sort('predicted_sentiment', ascending=False)[0]['review']

'I LOVE LOVE LOVE this product! It is SO much easier to use than the Diaper Genie, (you need a PHD in poopy to figure out how to use the darn thing!) and it even takes the same bags as my kitchen trash can, shich is super convenient, and cost efficient as I can buy them in bulk.The only reason for not rating it a 5 star was that I did have one small problem with it. The foam gasket in the barrell which keeps the poopy smell inside the unit ripped somehow, and it got VERY stinky. HOWEVER, I contacted the manufacturer though their website, and received an email back the same day stating that this was unusual, and that replacement gaskets were on their way to me. They arrived inside of a week and after replacing, it works great again! (They even sent me extras should it happen again)I HIGHLY reccomend this diaper pail over ANY competitors, you will not be sorry!'

In [98]:
selected_words_model.predict(diaper_champ_reviews.sort('predicted_sentiment', ascending=False)[0:1], output_type='probability')

dtype: float
Rows: 1
[0.9984234145936199]

In [100]:
diaper_champ_reviews['predicted_sentiment'] = sentiment_model.predict(diaper_champ_reviews, output_type='probability')
diaper_champ_reviews.sort('predicted_sentiment', ascending=False)

Columns:
	name	str
	review	str
	rating	float
	word_count	dict
	awesome	int
	great	int
	fantastic	int
	amazing	int
	love	int
	horrible	int
	bad	int
	terrible	int
	awful	int
	wow	int
	hate	int
	sentiment	int
	predicted_sentiment	float

Rows: 298

Data:
+-------------------------+-------------------------------+--------+
|           name          |             review            | rating |
+-------------------------+-------------------------------+--------+
| Baby Trend Diaper Champ | Baby Luke can turn a clean... |  5.0   |
| Baby Trend Diaper Champ | I LOOOVE this diaper pail!... |  5.0   |
| Baby Trend Diaper Champ | We researched all of the d... |  4.0   |
| Baby Trend Diaper Champ | My baby is now 8 months an... |  5.0   |
| Baby Trend Diaper Champ | This is absolutely, by far... |  5.0   |
| Baby Trend Diaper Champ | Diaper Champ or Diaper Gen... |  5.0   |
| Baby Trend Diaper Champ | Wow!  This is fabulous.  I... |  5.0   |
| Baby Trend Diaper Champ | I originally put this item... |  5.0   |
| Baby Trend Diaper Champ | Two girlfriends and two fa... |  5.0   |
| Baby Trend Diaper Champ | I am one of those super-cr... |  5.0   |
+-------------------------+-------------------------------+--------+
+-------------------------------+---------+-------+-----------+---------+------+
|           word_count          | awesome | great | fantastic | amazing | love |
+-------------------------------+---------+-------+-----------+---------+------+
| {'all': 1, 'less': 1, "fri... |    0    |   0   |     0     |    0    |  0   |
| {'just': 1, 'over': 1, 'rw... |    0    |   0   |     0     |    0    |  1   |
| {'all': 2, 'just': 4, "don... |    0    |   0   |     0     |    0    |  0   |
| {"don't": 1, 'when': 1, 'o... |    0    |   2   |     0     |    0    |  0   |
| {'just': 3, 'money': 1, 'n... |    0    |   0   |     0     |    0    |  2   |
| {'all': 1, 'bags.': 1, 'so... |    0    |   0   |     0     |    0    |  0   |
| {'and': 4, '"genie".': 1, ... |    0    |   0   |     0     |    0    |  0   |
| {'lysol': 1, 'all': 2, 'ba... |    0    |   0   |     0     |    0    |  0   |
| {'just': 1, 'when': 1, 'bo... |    0    |   0   |     0     |    0    |  0   |
| {'taller': 1, 'bags.': 1, ... |    0    |   0   |     0     |    0    |  1   |
+-------------------------------+---------+-------+-----------+---------+------+
+----------+-----+----------+-------+-----+------+-----------+---------------------+
| horrible | bad | terrible | awful | wow | hate | sentiment | predicted_sentiment |
+----------+-----+----------+-------+-----+------+-----------+---------------------+
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.999999937267   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.999999917406   |
|    0     |  1  |    0     |   0   |  0  |  0   |     1     |    0.999999899509   |
|    0     |  1  |    0     |   0   |  0  |  0   |     1     |    0.999999836182   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.999999824745   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.999999759315   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.999999692111   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.999999642488   |
|    1     |  0  |    0     |   0   |  0  |  0   |     1     |    0.999999604504   |
|    0     |  0  |    0     |   0   |  0  |  0   |     1     |    0.999999486804   |
+----------+-----+----------+-------+-----+------+-----------+---------------------+
[298 rows x 17 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.